## Step 1: Setting Up Optimum ExecuTorch

In [2]:
! touch /content/optimum-executorch; rm -rf /content/optimum-executorch
! git clone https://github.com/huggingface/optimum-executorch ; cd /content/optimum-executorch; pip install --pre executorch==0.6.0 torch==2.7.0 torchvision --extra-index-url "https://download.pytorch.org/whl/test/cpu"; pip install .; pip list

Cloning into 'optimum-executorch'...
remote: Enumerating objects: 533, done.
remote: Counting objects: 100% (234/234), done.
remote: Compressing objects: 100% (114/114), done.
remote: Total 533 (delta 168), reused 129 (delta 116), pack-reused 299 (from 2)
Receiving objects: 100% (533/533), 173.70 KiB | 5.26 MiB/s, done.
Resolving deltas: 100% (275/275), done.
Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/test/cpu
INFO: pip is looking at multiple versions of torchvision to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 176.0/176.0 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 5.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.2/6.2 MB 12.3 MB/s eta 0:00:00
  Attempting uninstall: sympy
    Found existing installation: sympy 1.13.1
    Uninstalling sympy-1.13.1:
      Successfully uninstalled sympy-1.13.1
  Attempting uninst

## Step 2: Export to ExecuTorch

In [3]:
! cd /content/optimum-executorch; optimum-cli export executorch \
  --model "HuggingFaceTB/SmolLM2-135M" \
  --task "text-generation" \
  --recipe "xnnpack" \
  --output_dir="./smollmv2_135m_custom_sdpa" \
  --use_custom_sdpa

! cd /content/optimum-executorch; ls -all ./smollmv2_135m_custom_sdpa

2025-04-11 21:20:23.780684: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1744406423.808206    7311 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1744406423.816142    7311 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-04-11 21:20:23.843321: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
config.json: 100% 704/704 [00:00<00:00, 3.09MB/s]
model.safetensors: 100% 269M/269M [00:01<00:00, 173MB/s]
/usr/local/lib/pyt

In [6]:
from optimum.executorch import ExecuTorchModelForCausalLM
from transformers import AutoTokenizer

# Load the exported model
model = ExecuTorchModelForCausalLM.from_pretrained("/content/optimum-executorch/smollmv2_135m_custom_sdpa")

# Initialize tokenizer and generate text
generated_text = model.text_generation(
    tokenizer=AutoTokenizer.from_pretrained("HuggingFaceTB/SmolLM2-135M"),
    prompt="Simply put, the theory of relativity states that",
    max_seq_len=32
)
print(generated_text)

[program.cpp:135] InternalConsistency verification requested but not available


PyTorchObserver {"prompt_tokens": 9, "generated_tokens": 23, "model_load_start_ms": 0, "model_load_end_ms": 0, "inference_start_ms": 1744406841892, "token_encode_end_ms": 1744406841892, "model_execution_start_ms": 1744406850941, "model_execution_end_ms": 1744406851168, "inference_end_ms": 1744406851169, "prompt_eval_end_ms": 1744406845805, "first_token_ms": 1744406846041, "aggregate_sampling_time_ms": 9271, "SCALING_FACTOR_UNITS_PER_SECOND": 1000}
	Prompt Tokens: 9 Generated Tokens: 23
	Model Load Time:		0.000000 (seconds)
	Total inference time:		9.277000 (seconds)		 Rate: 	2.479250 (tokens/second)
		Prompt evaluation:	3.913000 (seconds)		 Rate: 	2.300026 (tokens/second)
		Generated 23 tokens:	5.364000 (seconds)		 Rate: 	4.287845 (tokens/second)
	Time to first generated token:	4.149000 (seconds)
	Sampling time over 32 tokens:	9.271000 (seconds)
Simply put, the theory of relativity states that the speed of light is constant, regardless of the speed of the observer. This is a very import